In [1]:
!pip install datasets evaluate transformers[sentencepiece]

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 452 kB 27.4 MB/s 
     |████████████████████████████████| 81 kB 10.3 MB/s 
     |████████████████████████████████| 5.8 MB 81.8 MB/s 
     |████████████████████████████████| 132 kB 93.6 MB/s 
     |████████████████████████████████| 182 kB 92.9 MB/s 
     |████████████████████████████████| 212 kB 94.2 MB/s 
     |████████████████████████████████| 127 kB 85.8 MB/s 
     |████████████████████████████████| 7.6 MB 64.1 MB/s 
     |████████████████████████████████| 1.3 MB 83.6 MB/s 
  Attempting uninstall: urllib3
    Found existing installation: urllib3 1.24.3
    Uninstalling urllib3-1.24.3:
      Successfully uninstalled urllib3-1.24.3


In [2]:
from datasets import load_dataset

indic_dataset = load_dataset('aashay96/indic-gpt')

Computing checksums:  86%|########5 | 6/7 [00:05<00:00,  1.15it/s]

Extracting data files:   0%|          | 0/1 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

Dataset parquet downloaded and prepared to /root/.cache/huggingface/datasets/aashay96___parquet/aashay96--indic-gpt-da3c02d4222f9683/0.0.0/2a3b91fbd88a2c90d1dbbb32b460cf621d31bd5b05b934492fdef7d8d6f236ec. Subsequent calls will reuse this data.


  0%|          | 0/1 [00:00<?, ?it/s]

In [3]:
indic_dataset = indic_dataset['train'].train_test_split(test_size=0.1)

In [4]:
from tokenizers import (
    decoders,
    models,
    normalizers,
    pre_tokenizers,
    processors,
    trainers,
    Tokenizer,
)

tokenizer = Tokenizer(models.BPE())


In [5]:
indic_dataset

DatasetDict({
    train: Dataset({
        features: ['text'],
        num_rows: 11454023
    })
    test: Dataset({
        features: ['text'],
        num_rows: 1272670
    })
})

In [ ]:
tokenizer.pre_tokenizer = pre_tokenizers.ByteLevel(add_prefix_space=False)
tokenizer.pre_tokenizer.pre_tokenize_str("জায়গামতো পৌঁছানো গেছে মনে করে মনে মনে হাঁফ ছাড়ে বরকত আলী।")

In [7]:
trainer = trainers.BpeTrainer(vocab_size=60000, special_tokens=["<|endoftext|>"])
tokenizer.train_from_iterator(indic_dataset['train']['text'], trainer=trainer)

In [8]:
tokenizer.post_processor = processors.ByteLevel(trim_offsets=False)

In [36]:
encoding = tokenizer.encode("জায়গামতো পৌঁছানো গেছে মনে করে মনে মনে হাঁফ ছাড়ে বরকত আলী।")
print(encoding.tokens)

['à¦ľ', 'à¦¾', 'à§Łà¦Ĺ', 'à¦¾', 'à¦®à¦¤', 'à§ĭ', 'Ġà¦ª', 'à§ĩà§Ĺà¦ģ', 'à¦Ľ', 'à¦¾', 'à¦¨', 'à§ĭ', 'Ġà¦Ĺ', 'à§ĩ', 'à¦Ľ', 'à§ĩ', 'Ġà¦®à¦¨', 'à§ĩ', 'Ġà¦ķà¦°', 'à§ĩ', 'Ġà¦®à¦¨', 'à§ĩ', 'Ġà¦®à¦¨', 'à§ĩ', 'Ġà¦¹', 'à¦¾à¦ģ', 'à¦«', 'Ġà¦Ľ', 'à¦¾', 'à§ľ', 'à§ĩ', 'Ġà¦¬à¦°à¦ķà¦¤', 'Ġà¦Ĩà¦²', 'à§Ģà¥¤']


In [9]:
sentence = "জায়গামতো পৌঁছানো গেছে মনে করে মনে মনে হাঁফ ছাড়ে বরকত আলী।"
encoding = tokenizer.encode(sentence)
start, end = encoding.offsets[4]
sentence[start:end]

'মত'

In [10]:
tokenizer.decoder = decoders.ByteLevel()

tokenizer.decode(encoding.ids)

'জায়গামতো পৌঁছানো গেছে মনে করে মনে মনে হাঁফ ছাড়ে বরকত আলী।'

In [11]:
from transformers import PreTrainedTokenizerFast

fast_tokenizer = PreTrainedTokenizerFast(tokenizer_object=tokenizer,bos_token="<|endoftext|>",
    eos_token="<|endoftext|>")

In [12]:
def tokenize(element):
    outputs = fast_tokenizer(
        element['text'],
        truncation=True,
        max_length=128,
        return_overflowing_tokens=True,
        return_length=True,
    )
    input_batch = []
    for length, input_ids in zip(outputs["length"], outputs["input_ids"]):
        if length == 128:
            input_batch.append(input_ids)
    return {"input_ids": input_batch}


tokenized_datasets = indic_dataset.map(
    tokenize, batched=True, remove_columns=indic_dataset["train"].column_names
)
tokenized_datasets

  0%|          | 0/11455 [00:00<?, ?ba/s]

  0%|          | 0/1273 [00:00<?, ?ba/s]

DatasetDict({
    train: Dataset({
        features: ['input_ids'],
        num_rows: 1681591
    })
    test: Dataset({
        features: ['input_ids'],
        num_rows: 187231
    })
})

In [13]:
from transformers import AutoTokenizer, GPT2LMHeadModel, AutoConfig

config = AutoConfig.from_pretrained(
    'gpt2',
    vocab_size=len(fast_tokenizer),
    n_ctx=128,
    bos_token_id=fast_tokenizer.bos_token_id,
    eos_token_id=fast_tokenizer.eos_token_id,
)

Downloading:   0%|          | 0.00/665 [00:00<?, ?B/s]

In [35]:
model = GPT2LMHeadModel(config)
model_size = sum(t.numel() for t in model.parameters())
print(f"GPT-2 size: {model_size/1000**2:.1f}M parameters")

GPT-2 size: 131.9M parameters


In [36]:
from transformers import DataCollatorForLanguageModeling

#for some reason this doesn't work
fast_tokenizer.pad_token = fast_tokenizer.eos_token
data_collator = DataCollatorForLanguageModeling(fast_tokenizer, mlm=False)


In [16]:
out = data_collator([tokenized_datasets["train"][i] for i in range(5)])
for key in out:
    print(f"{key} shape: {out[key].shape}")


You're using a PreTrainedTokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


input_ids shape: torch.Size([5, 128])
attention_mask shape: torch.Size([5, 128])
labels shape: torch.Size([5, 128])


In [17]:
from huggingface_hub import notebook_login

notebook_login()


Token is valid.
Your token has been saved in your configured git credential helpers (store).
Your token has been saved to /root/.huggingface/token
Login successful


In [37]:
from transformers import Trainer, TrainingArguments

args = TrainingArguments(
    output_dir="indic-gpt/",
    per_device_train_batch_size=128,
    per_device_eval_batch_size=128,
    evaluation_strategy="steps",
    eval_steps=5000,
    logging_steps=5000,
    gradient_accumulation_steps=8,
    num_train_epochs=1,
    weight_decay=0.1,
    warmup_steps=1000,
    lr_scheduler_type="cosine",
    learning_rate=5e-4,
    save_steps=5000,
    fp16=True,
    push_to_hub=True,
)

trainer = Trainer(
    model=model,
    tokenizer=fast_tokenizer,
    args=args,
    data_collator=data_collator,
    train_dataset=tokenized_datasets["train"],
    eval_dataset=tokenized_datasets["test"],
)

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).
/content/indic-gpt/ is already a clone of https://huggingface.co./aashay96/indic-gpt. Make sure you pull the latest changes with `repo.git_pull()`.
Using cuda_amp half precision backend


In [38]:
trainer.train()

/usr/local/lib/python3.8/dist-packages/transformers/optimization.py:306: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
***** Running training *****
  Num examples = 1681591
  Num Epochs = 1
  Instantaneous batch size per device = 128
  Total train batch size (w. parallel, distributed & accumulation) = 1024
  Gradient Accumulation steps = 8
  Total optimization steps = 1642
  Number of trainable parameters = 131922432


Saving model checkpoint to indic-gpt/checkpoint-200
Configuration saved in indic-gpt/checkpoint-200/config.json
Model weights saved in indic-gpt/checkpoint-200/pytorch_model.bin
tokenizer config file saved in indic-gpt/checkpoint-200/tokenizer_config.json
Special tokens file saved in indic-gpt/checkpoint-200/special_tokens_map.json
tokenizer config file saved in indic-gpt/tokenizer_config.json
Special tokens file saved in indic-gpt/special_tokens_map.json
Several commits (3) will be pushed upstream.
Saving model checkpoint to indic-gpt/checkpoint-400
Configuration saved in indic-gpt/checkpoint-400/config.json
Model weights saved in indic-gpt/checkpoint-400/pytorch_model.bin
tokenizer config file saved in indic-gpt/checkpoint-400/tokenizer_config.json
Special tokens file saved in indic-gpt/checkpoint-400/special_tokens_map.json
***** Running Evaluation *****
  Num examples = 187231
  Batch size = 128
Saving model checkpoint to indic-gpt/checkpoint-600
Configuration saved in indic-gpt/ch

TrainOutput(global_step=1642, training_loss=2.491443406359432, metrics={'train_runtime': 4251.4905, 'train_samples_per_second': 395.53, 'train_steps_per_second': 0.386, 'total_flos': 1.09834628235264e+17, 'train_loss': 2.491443406359432, 'epoch': 1.0})

In [39]:
trainer.push_to_hub()

Saving model checkpoint to indic-gpt/
Configuration saved in indic-gpt/config.json
Model weights saved in indic-gpt/pytorch_model.bin
tokenizer config file saved in indic-gpt/tokenizer_config.json
Special tokens file saved in indic-gpt/special_tokens_map.json
Several commits (4) will be pushed upstream.
The progress bars may be unreliable.


Upload file pytorch_model.bin:   0%|          | 3.30k/515M [00:00<?, ?B/s]

Upload file runs/Dec22_10-11-35_40549f43bb54/events.out.tfevents.1671703904.40549f43bb54.1064.13:  60%|###### …

remote: Scanning LFS files for validity, may be slow...        
remote: LFS file scan complete.        
To https://huggingface.co./aashay96/indic-gpt
   8dab26e..6693b9d  main -> main

remote: LFS file scan complete.        
To https://huggingface.co./aashay96/indic-gpt
   8dab26e..6693b9d  main -> main

Dropping the following result as it does not have all the necessary fields:
{'task': {'name': 'Causal Language Modeling', 'type': 'text-generation'}}
To https://huggingface.co./aashay96/indic-gpt
   6693b9d..07e4411  main -> main

   6693b9d..07e4411  main -> main



'https://huggingface.co./aashay96/indic-gpt/commit/6693b9dbf14b8036692ca0477ff44fd1a9e3bd4b'